In [1]:
%matplotlib qt
import numpy as np
from numpy.random import rand
from landscapeWithOcean import LandscapeWithOcean
from mpl_toolkits.mplot3d import Axes3D
import matplotlib.pyplot as plt
from matplotlib import cm

In [2]:
def AddHill(Z,NX,NY,xx,yy,r,h):

    for x in range(NX):
        for y in range(NY):
            dx = np.mod(x-xx+NX/2,NX)-NX/2; # difference i-i0 but apply p.b.c. 
            dy = np.mod(y-yy+NY/2,NY)-NY/2;
            dr = np.sqrt(dx**2+dy**2);
            if (dr < r/4):
                Z[x,y] = h 
            elif dr >= r/4 and dr < r:
                Z[x,y]= 4*h/3*(1-dr/r)
            

    return Z

In [3]:
def AddHill2(Z,NX,NY,xx,yy,r,h):

    for x in range(NX):
        for y in range(NY):
            dx = np.mod(x-xx+NX/2,NX)-NX/2; # difference i-i0 but apply p.b.c. 
            dy = np.mod(y-yy+NY/2,NY)-NY/2;
            dr = np.sqrt(dx**2+dy**2);
            if (dr < r/3):
                Z[x,y] = (3*h/4*r)*(dr-r/3)+h
            
            elif dr >= r/3 and dr < r:
                Z[x,y]= (-3*h/(2*r))*(dr-r)
            
    return Z

In [4]:
### Define simulation grid and initial conditions

NX = 400 #number of rows Grid or matrix size
NY = 400 #number of columns

d  = 5 # grid spacing in meters
dx = d # Cell size
dy = d

LX=NX*dx
LY=NY*dy

# small random features in topography to begin erosion
xs=[NX//2]
ys=[NY//2]


Z = np.zeros((NX,NY))-10
for i in range(1):
    xx = xs[i]
    yy = ys[i]
    r  = (0.8*NX)
    h  = 50
    Z = AddHill(Z,NX,NY,xx,yy,r,h)


ZMaxOrg = np.max(Z)

In [5]:
### Physical Parameters
K = 1.0e-6 # meters^(1-2m)/yr

D = 0.0214 # m^2/yr

# uplift rate
# uplift = 0.03 / 600.
uplift = 0.0

In [6]:
### Model parameters  Parameters and initial values for the finite-difference grid and modeled scoria cone

# Time step
dt = d**2 / D / 8. 
#dt = d**2 / D /16. #extra small steps
dt = 100
print(' dt[years] = ',dt)

#Area exponent A^m, default m=1
m=1.2

#gradient exponent g^n, default n=1
n=1

#erosion threshold 
theta_c = 10 

 dt[years] =  100


In [7]:
# Total simulation time
T = 200 * 100.0

# total number of iterations
n_iter = int(np.round(T/dt))
print('Number of interation: ',n_iter)

Number of interation:  200


In [8]:
# Initialize landscape 
ls = LandscapeWithOcean(NX,NY)

oceanLevelParameter=0.3  # what does this parameter do?
ls.ComputeOceanVolumeFromOceanLevelParameter(Z,NX,NY,oceanLevelParameter)

ls.pool_check(Z,NX,NY)
ls.A = np.zeros((NX,NY))

Minimum elevation           7.741101567787704
Maximum elevation           50.0
Beach level                 20.418771097451394
Ocean volume                67591.82677826716
Percentage of ocean surface 10.380625


In [9]:
# Set-up figure
def init_figure():
    fig = plt.figure(figsize=(12.,6.))
    return fig

def update_figure():
    global Z
    plt.clf()
    ax1 = fig.add_subplot(121,projection='3d')

    # use equal x-y aspect with an explicit vertical exageration
    vert_exag = 2.
    L = 400
    ax1.set_xlim3d(0,L)
    ax1.set_ylim3d(0,L)
    ax1.set_zlim3d(0,ZMaxOrg)

    ax1.set_title('Surface Relief')

#        surf = ax1.plot_surface(X,Y,Z, cmap = cm.terrain, rstride=1, cstride=1,
#                antialiased=False,linewidth=0)

    ZPlot = np.copy(Z)
    ZPlot[ZPlot<ls.ZBeachLevel] = ls.ZBeachLevel 
    ZPlot -= ls.ZBeachLevel
    X = np.linspace(0,L,NX)
    Y = np.linspace(0,L,NY)
    X,Y = np.meshgrid(X,Y)
    ax1.plot_surface(X,Y,ZPlot, cmap = cm.terrain, rstride=1, cstride=1,
            antialiased=False,linewidth=0)

    ax2 = fig.add_subplot(122,aspect='equal')
    ax2.set_title('Elevation')

    #im = ax2.pcolor(Z,cmap=cm.terrain)
    im = ax2.pcolor(ZPlot,cmap=cm.coolwarm)
    cs = ax2.contour(ZPlot,6,colors='k')

    # Add a color bar which maps values to colors.
    cbar = fig.colorbar(im, shrink=0.5, aspect=5)
    # Add the contour line levels to the colorbar
    cbar.add_lines(cs)

    plt.show()
    plt.draw()
    plt.pause(0.0001)

In [ ]:
Z = np.zeros((NX,NY))
for i in range(1):
    xx = xs[i]
    yy = ys[i]
    r  = (0.7*NX)
    h  = 60
    Z = AddHill2(Z,NX,NY,xx,yy,r,h)

fig = init_figure()
update_figure()
Znew = np.copy(Z)
from matplotlib.animation import FFMpegWriter

metadata = dict(title='My first animation in 3D', artist='Matplotlib',comment='Wakanda is here now.')
writer = FFMpegWriter(fps=15, metadata=metadata,bitrate=200000)

with writer.saving(fig, "Final project f2.mp4", dpi=200):

    for it in range(1,200+1):
        writer.grab_frame()
        ls.calculate_collection_area(Z,NX,NY)
        ls.A *= dx*dy
        print("it = {}".format(it))

        for i in range(NX):
            iL = np.mod(i-1,NX) # normally i-1 but observe p.b.c.
            iR = np.mod(i+1,NX) # normally i+1 but observe p.b.c.

            for j in range(NY):
                jD = np.mod(j-1,NY) # normally j-1 but observe p.b.c.
                jU = np.mod(j+1,NY) # normally j+1 but observe p.b.c.

                if ls.ocean[i,j]>0:
                    Psi_z  = 0;
                    Phi_z  = 0;
                else:
                    if ls.drain[i,j]>0: #this cell is a drain
                        s1 = (Z[iR,j]  - Z[iL,j] )/(2.*dx)
                        s2 = (Z[i,jU]  - Z[i,jD] )/(2.*dy)
                        s3 = (Z[iR,jD] - Z[iL,jU])/(2. * np.sqrt( dx**2 + dy**2) )
                        s4 = (Z[iR,jU] - Z[iL,jD])/(2. * np.sqrt( dx**2 + dy**2) )
                        gradient = (np.sqrt(s1**2 + s2**2) + np.sqrt(s3**2 + s4**2))/2.
                        Psi_z = K * ( ls.A[i,j]**m * gradient**n - theta_c)            

                    elif ls.drainage[i,j]>0: #this cell is a drainage point (it drains a pool)

                        if (Z[i,j]>=Z[iR,j]) and ls.pool[iR,j]!=ls.drainage[i,j]: 
                            gradient = (Z[i,j]-Z[iR,j])/dx #pool is on my left, I drain to the right, use this gradiant
                        elif (Z[i,j]>=Z[iL,j]) and ls.pool[iL,j]!=ls.drainage[i,j]:
                            gradient = (Z[i,j]-Z[iL,j])/dx
                        elif (Z[i,j]>=Z[i,jU]) and ls.pool[i,jU]!=ls.drainage[i,j]:
                            gradient = (Z[i,j]-Z[i,jU])/dy
                        elif (Z[i,j]>=Z[i,jD]) and ls.pool[i,jD]!=ls.drainage[i,j]:
                            gradient = (Z[i,j]-Z[i,jD])/dy
                        else:
                            gradient = 0.02 # ??? This does happen (maybe when two pools merge)
                        Psi_z = K * ( ls.A[i,j]**m * gradient**n - theta_c)

                    else: #this cell is a pool, assume it has some mass diffusion but no erosion!
                        Psi_z = 0.

                    if (Psi_z<0):
                        Psi_z = 0. 

                    # diffusion term
                    Phi_z = D * ( (Z[iR,j] - 2.*Z[i,j] + Z[iL,j]) / dx**2 \
                                + (Z[i,jU] - 2.*Z[i,j] + Z[i,jD]) / dx**2 )

                Znew[i,j] = Z[i,j] + (Phi_z - Psi_z + uplift )*dt  

                dZdt= (Znew[i,j] - Z[i,j]) / dt
                CFL = abs(dZdt) * dt / min(dx,dy)
                if (CFL>1.0):
                    print('\nWarning: Time step of',dt,'is probably too large. Safer would be:',dt/CFL)

                if (Znew[i,j]<0.):
                    Znew[i,j] = 0. # yes, this does happen at the boundary when kept at zero

        #Znew[0,:] = 0.0 # resets front boundary to 0
        Z = np.copy(Znew)

        ls.pool_check(Z,NX,NY)

        if (np.mod(it,5)==0): 
            print(it,end='')
            update_figure()
            print(' Ocean level=',ls.ZBeachLevel,' Ocean surface fraction=',100*ls.AOcean/(NX*NY));
        else:
            print('.',end='')

    update_figure()
    print(' Simulation finished.')

it = 1














































































































































































































































































































.it = 2






































































































































































































.it = 3















































































































.it = 4












































































































.it = 5
























































...











































.it = 30
































30 Ocean level= 2.2990932708711758  Ocean surface fraction= 19.571875
it = 31


































.it = 32




























































.it = 33










































































.it = 34
































.it = 35






































































35 Ocean level= 2.287297201839925  Ocean surface fraction= 19.77375
it = 36






































































.it = 37
































































.it = 38
























.